# BostonHousing.csv column name exlanation

* CRIM - per capita crime rate by town
* ZN - proportion of residential land zoned for lots over 25,000 sq.ft.
* INDUS - proportion of non-retail business acres per town.
* CHAS - Charles River dummy variable (1 if tract bounds river; 0 otherwise)
* NOX - nitric oxides concentration (parts per 10 million)
* RM - average number of rooms per dwelling
* AGE - proportion of owner-occupied units built prior to 1940
* DIS - weighted distances to five Boston employment centres
* RAD - index of accessibility to radial highways
* TAX - full-value property-tax rate per $10,000
* PTRATIO - pupil-teacher ratio by town
* B - 1000(Bk - 0.63)^2 where Bk is the proportion of blacks by town
* LSTAT - % lower status of the population
* MEDV - Median value of owner-occupied homes in $1000's

In [5]:
# prompt: read bostonhousing.csv

import pandas as pd

# Assuming your CSV file is in your Google Drive's My Drive folder
file_path = 'BostonHousing.csv'

try:
  df = pd.read_csv(file_path)
  print(df.head())  # Display the first few rows of the DataFrame
except FileNotFoundError:
  print(f"File not found at: {file_path}")


      crim    zn  indus  chas    nox     rm   age     dis  rad  tax  ptratio  \
0  0.00632  18.0   2.31     0  0.538  6.575  65.2  4.0900    1  296     15.3   
1  0.02731   0.0   7.07     0  0.469  6.421  78.9  4.9671    2  242     17.8   
2  0.02729   0.0   7.07     0  0.469  7.185  61.1  4.9671    2  242     17.8   
3  0.03237   0.0   2.18     0  0.458  6.998  45.8  6.0622    3  222     18.7   
4  0.06905   0.0   2.18     0  0.458  7.147  54.2  6.0622    3  222     18.7   

        b  lstat  medv  
0  396.90   4.98  24.0  
1  396.90   9.14  21.6  
2  392.83   4.03  34.7  
3  394.63   2.94  33.4  
4  396.90   5.33  36.2  


In [7]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
import statsmodels.api as sm


In [13]:
X = df.drop(['medv'], axis=1)
y = pd.Series(df.medv, name='PRICE')


In [14]:
# Step 1: Dummify (One-Hot Encode) the 'RAD' column
# RAD: index of accessibility to radial highways (categorical)
X['rad'] = X['rad'].astype(int)  # Ensure it's treated as an integer categorical column
X = pd.get_dummies(X, columns=['rad'], drop_first=True)  # Drop first to avoid multicollinearity


In [15]:
# Check for non-numeric columns
non_numeric_cols = X.select_dtypes(exclude=np.number).columns
print(f"Non-numeric columns: {non_numeric_cols}") # Print out any non-numeric columns


Non-numeric columns: Index(['rad_2', 'rad_3', 'rad_4', 'rad_5', 'rad_6', 'rad_7', 'rad_8',
       'rad_24'],
      dtype='object')


In [16]:
X.head()

crim    zn  indus  chas    nox     rm   age     dis  tax  ptratio  \
0  0.00632  18.0   2.31     0  0.538  6.575  65.2  4.0900  296     15.3   
1  0.02731   0.0   7.07     0  0.469  6.421  78.9  4.9671  242     17.8   
2  0.02729   0.0   7.07     0  0.469  7.185  61.1  4.9671  242     17.8   
3  0.03237   0.0   2.18     0  0.458  6.998  45.8  6.0622  222     18.7   
4  0.06905   0.0   2.18     0  0.458  7.147  54.2  6.0622  222     18.7   

        b  lstat  rad_2  rad_3  rad_4  rad_5  rad_6  rad_7  rad_8  rad_24  
0  396.90   4.98  False  False  False  False  False  False  False   False  
1  396.90   9.14   True  False  False  False  False  False  False   False  
2  392.83   4.03   True  False  False  False  False  False  False   False  
3  394.63   2.94  False   True  False  False  False  False  False   False  
4  396.90   5.33  False   True  False  False  False  False  False   False

In [17]:
# prompt: convert non_numeric_cols in the dataframe to interger type by replace True = 1 and False = 0

# Assuming 'X' is your DataFrame and 'non_numeric_cols' contains the non-numeric columns
for col in non_numeric_cols:
  X[col] = X[col].astype(int)


In [18]:
# Step 2: Add constant for intercept
X_const = sm.add_constant(X)

# Step 3: Split the data into train and test sets
X_trainf, X_testf, y_trainf, y_testf = train_test_split(X_const, y, test_size=0.2, random_state=42)

# Step 4: Build the multiple linear regression model without interaction terms
model_full = sm.OLS(y_trainf, X_trainf).fit()
print("Model Full:\n")
print(model_full.summary())

Model Full:

                            OLS Regression Results                            
Dep. Variable:                  PRICE   R-squared:                       0.763
Model:                            OLS   Adj. R-squared:                  0.750
Method:                 Least Squares   F-statistic:                     61.59
Date:                Thu, 19 Sep 2024   Prob (F-statistic):          2.26e-106
Time:                        17:06:34   Log-Likelihood:                -1184.4
No. Observations:                 404   AIC:                             2411.
Df Residuals:                     383   BIC:                             2495.
Df Model:                          20                                         
Covariance Type:            nonrobust                                         
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
const         28.9224      6.044      4

In [19]:
# Step 5: Add interaction term (LSTAT * RM)
X['LSTAT_RM_Interaction'] = X['lstat'] * X['rm']

# Add constant term again for the model with interaction
X_with_interaction_const = sm.add_constant(X)

# Step 6: Split the interaction dataset into train and test sets
X_train_interaction, X_test_interaction, y_train_interaction, y_test_interaction = train_test_split(X_with_interaction_const, y, test_size=0.2, random_state=42)

# Step 7: Build the multiple linear regression model with interaction terms
model_with_interaction = sm.OLS(y_train_interaction, X_train_interaction).fit()
print("\nModel with Interaction Terms:\n")
print(model_with_interaction.summary())


Model with Interaction Terms:

                            OLS Regression Results                            
Dep. Variable:                  PRICE   R-squared:                       0.815
Model:                            OLS   Adj. R-squared:                  0.805
Method:                 Least Squares   F-statistic:                     80.34
Date:                Thu, 19 Sep 2024   Prob (F-statistic):          5.59e-126
Time:                        17:24:59   Log-Likelihood:                -1133.8
No. Observations:                 404   AIC:                             2312.
Df Residuals:                     382   BIC:                             2400.
Df Model:                          21                                         
Covariance Type:            nonrobust                                         
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------


The presence of an interaction indicates that the effect of one predictor variable on the response variable is different at different values of the other predictor variable.

Reference: https://aarongullickson.github.io/stat_book/interaction-terms.html

In [21]:
from statsmodels.stats.outliers_influence import variance_inflation_factor

# Calculate VIF Scores
vif_data = pd.DataFrame()
vif_data["feature"] = X.columns
#vif_data["VIF"] = [variance_inflation_factor(X.values, i+1) for i in range(X.shape[1])]
vif_data["VIF"] = [variance_inflation_factor(X.values, i) for i in range(X.shape[1])] # The index should start from 0 for the first column

print("VIF Scores before removing high VIF features:")
print(vif_data)

VIF Scores before removing high VIF features:
                 feature         VIF
0                   crim    2.171398
1                     zn    3.156594
2                  indus   15.951465
3                   chas    1.186896
4                    nox   88.591697
5                     rm  133.750526
6                    age   22.309314
7                    dis   15.454549
8                    tax   67.417818
9                ptratio  107.071630
10                     b   22.268511
11                 lstat  178.024370
12                 rad_2    2.293878
13                 rad_3    2.983141
14                 rad_4    6.890922
15                 rad_5    7.198941
16                 rad_6    2.426500
17                 rad_7    1.905462
18                 rad_8    2.435413
19                rad_24   19.143322
20  LSTAT_RM_Interaction  193.434543
